<a href="https://colab.research.google.com/github/maripkl/topic_modeling/blob/main/topic_modeling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Тематическое моделирование коротких текстовых сообщений
### Topic Modeling with Contextualized Word Representation Clusters
#### *Поклонская Мария*

Первым делом нам нужно подключить все необходимые библиотеки. 

In [ ]:
!pip install -U contextualized_topic_models

In [ ]:
from contextualized_topic_models.models.ctm import CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation
from contextualized_topic_models.utils.data_preparation import bert_embeddings_from_file
from contextualized_topic_models.utils.preprocessing import WhiteSpacePreprocessing
from contextualized_topic_models.models.ctm import ZeroShotTM


import nltk
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import random

Для начала загрузим данные с kaggle и приведем их в табличный вид для дальнейшего анализа. 

In [ ]:
from google.colab import files
files.upload()

Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"mariapoklonskaya","key":"927a746bbe6e2597bd9842ac5da7ede2"}'}

In [ ]:
!rm -r ~/.kaggle
!mkdir ~/.kaggle
!mv ./kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

rm: cannot remove '/root/.kaggle': No such file or directory


In [ ]:
!kaggle datasets download -d Cornell-University/arxiv

 99% 1.06G/1.07G [00:05<00:00, 179MB/s]
100% 1.07G/1.07G [00:05<00:00, 192MB/s]


In [ ]:
!unzip /content/arxiv.zip

Archive:  /content/arxiv.zip
  inflating: arxiv-metadata-oai-snapshot.json  


In [ ]:
import json

data_file = '/content/arxiv-metadata-oai-snapshot.json'

def get_metadata():
    with open(data_file, 'r') as f:
        for line in f:
            yield line

In [ ]:
metadata = get_metadata()
for paper in metadata:
    paper_dict = json.loads(paper)
    print('Title: {}\n\nAbstract: {}\nRef: {}'.format(paper_dict.get('title'), paper_dict.get('abstract'), paper_dict.get('journal-ref')))
    break

Title: Calculation of prompt diphoton production cross sections at Tevatron and
  LHC energies

Abstract:   A fully differential calculation in perturbative quantum chromodynamics is
presented for the production of massive photon pairs at hadron colliders. All
next-to-leading order perturbative contributions from quark-antiquark,
gluon-(anti)quark, and gluon-gluon subprocesses are included, as well as
all-orders resummation of initial-state gluon radiation valid at
next-to-next-to-leading logarithmic accuracy. The region of phase space is
specified in which the calculation is most reliable. Good agreement is
demonstrated with data from the Fermilab Tevatron, and predictions are made for
more detailed tests with CDF and DO data. Predictions are shown for
distributions of diphoton pairs produced at the energy of the Large Hadron
Collider (LHC). Distributions of the diphoton pairs from the decay of a Higgs
boson are contrasted with those produced from QCD processes at the LHC, showing
tha

У нас есть ограничения по памяти, поэтому мы не можем использовать весь датасет. Давайте будем анализировать данные начиная с 2012 года. 

In [ ]:
titles = []
ids = []
abstracts = []
authors_parsed = []
authors = []
years = []
metadata = get_metadata()
for paper in metadata:
    paper_dict = json.loads(paper)
    ref = paper_dict.get('journal-ref')
    try:
        year = int(ref[-4:]) 
        if 2011 < year <= 2022:
            years.append(year)
            ids.append(paper_dict.get('id'))
            authors_parsed.append(paper_dict.get('authors_parsed'))
            authors.append(paper_dict.get('authors'))
            titles.append(paper_dict.get('title'))
            abstracts.append(paper_dict.get('abstract'))
    except:
        pass 

len(titles), len(abstracts), len(years)

(43668, 43668, 43668)

In [ ]:
papers = pd.DataFrame({
    'id' : ids,
    'title': titles,
    'authors': authors,
    'authors parsed': authors_parsed,
    'abstract': abstracts,
    'year': years
})
papers.head()

id                                              title  \
0  0704.0304                  The World as Evolving Information   
1  0704.0498  A unified analysis of the reactor neutrino pro...   
2  0704.2768  Heat Equations and the Weighted $\bar\partial$...   
3  0705.0505  Non Supersymmetric Metastable Vacua in N=2 SYM...   
4  0705.0681  Entanglement in a Jaynes-Cummings Model with T...   

                                             authors  \
0                                  Carlos Gershenson   
1  Guillaume Mention (DAPNIA), Thierry Lasserre (...   
2                                       Andrew Raich   
3                                   Georgios Pastras   
4                  Samina S. Masood and Allen Miller   

                                      authors parsed  \
0                           [[Gershenson, Carlos, ]]   
1  [[Mention, Guillaume, , DAPNIA], [Lasserre, Th...   
2                                [[Raich, Andrew, ]]   
3                            [[Pastras, Georgios, ]]   
4         [[Masood, Samina S., ], [Miller, Allen, ]]   

                                            abstract  year  
0    This paper discusses the benefits of describ...  2012  
1    We present in this article a detailed quanti...  2013  
2    The purpose of this article is to establish ...  2012  
3    We find non-supersymmetric metastable vacua ...  2013  
4    We investigate the conditions of entanglemen...  2014

Дальнейший анализ будет строиться на столбце "Abstract", в котором собраны аннотации к статьям. 

При работе модели используются два вида данных - предобработанные для построения мешка слов и необработанные для построения предобученных векторных эмбеддингов BERT. 

Обрабатывать данные мы будем следующим образом: переведем все в нижний регистр, исключим знаки пунктуации, числа и лишние слова (предлоги, местоимения и т. д.) при помощи Natural Language Toolkit. 

In [ ]:
import string
documents = papers.abstract.to_list()
nltk.download('punkt')
nltk.download('stopwords')

from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize
stop_words = set(stopwords.words('english'))
def process_text(text, stop_words=stop_words):
    return ' '.join([word for word in word_tokenize(text.lower()) if (word not in string.punctuation and word not in stop_words and not word.isdigit())])

preprocessed = papers.abstract.apply(process_text)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


Ниже мы видим какие получаются данные для построения мешка слов:

In [ ]:
preprocessed[:4]

0    paper discusses benefits describing world info...
1    present article detailed quantitative discussi...
2    purpose article establish regularity pointwise...
3    find non-supersymmetric metastable vacua four ...
Name: abstract, dtype: object

В семействе CTM представлены две модели CombinedTM и ZeroShotTM. Разница заключается в том, что первая модель работает с комбинацией контекстуальных эмбеддингов и BoW, ее целью является создание осмысленных согласованных тем, а вторая модель принимает только контекстуальные эмбеддинги и направлена на то, чтобы уметь обрабатывать неизвестные новые слова на этапе тестирования и применяться к другим языкам без больших вычислительных сложностей. 

###Начнем с изучения модели CombinedTM. 

Для создания набора данных для обучения модели передадим предварительно обработанные и необработанные данные объекту TopicModelDataPreparation, который создаст мешок слов и получит контекстуальные представления BERT всех документов. Таким образом мы создадим набор данных для обучения в подходящим для этой модели виде. 

У самой модели несколько параметров:

- bow_size - размер словаря
- contextual_size - размер контекстуальных эмбеддингов
- n_components - количество тем, которые мы хотим получить от модели
- num_epochs - количество эпох для обучения

Мы будем использовать контекстуальную модель "paraphrase-distilroberta-base-v2", так как она работает с представлениями предложений и абзацев, что соответствует требованиям используемой модели. 

In [ ]:
# создаем датасет для обучения
qt = TopicModelDataPreparation("paraphrase-distilroberta-base-v2")
training_dataset = qt.fit(text_for_contextual=documents, text_for_bow=preprocessed)

Downloading:   0%|          | 0.00/736 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/3.74k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/686 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/122 [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/798k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/229 [00:00<?, ?B/s]

/usr/local/lib/python3.7/dist-packages/contextualized_topic_models/utils/data_preparation.py:57: UserWarning: the longest document in your collection has 444 words, the model instead truncates to 128 tokens.
  warnings.warn(f"the longest document in your collection has {max_local_length} words, the model instead "


Batches:   0%|          | 0/219 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


Может быть интересно взглянуть на словарь, который мы получили:

In [ ]:
print(random.sample(qt.vocab, 15))

['dutton', 'embeddding', 'uninterrupted', 'chaplygin', 'liter', 'unrealized', 'capturable', '252no', 'mininet', 'involuntary', 'internodons', 'k5', 'ekiti', 'adenocarcinoma', 'optimisers']


Мы видим, что словарь в основном состоит из научных терминов без каких-то малозначащих ненужных слов, а значит из таких слов и темы должны быть более осмысленные (чем если бы мы описывали темы через местоимения или числа)

In [ ]:
# обучаем модель
ctm = CombinedTM(bow_size=len(qt.vocab), contextual_size=768, n_components=50, num_epochs=15) 
ctm.fit(training_dataset) 

Epoch: [15/15]	 Seen Samples: [655020/655020]	Train Loss: 1020.055829640698	Time: 0:00:41.043169: : 15it [10:02, 40.15s/it]
Sampling: [20/20]: : 20it [09:09, 27.50s/it]


Теперь посмотрим на темы, которые получила наша модель после обучения, всего их 50. 

При помощи параметра в методе get_topics мы можем выбирать какое количество слов будут характеризовать каждую тему. 

In [ ]:
ctm.get_topics(5)

defaultdict(list,
            {0: ['disease', 'population', 'clinical', 'treatment', 'brain'],
             1: ['quantum', 'classical', 'entanglement', 'codes', 'channels'],
             2: ['relieve', 'regressive', 'accumulates', '785', 'tion'],
             3: ['ray', 'emission', 'spectral', 'sources', 'detected'],
             4: ['temperature',
              'temperatures',
              'diffraction',
              'atomic',
              'molecules'],
             5: ['agents', 'agent', 'strategies', 'strategy', 'game'],
             6: ['security', 'services', 'smart', 'internet', 'application'],
             7: ['reconstruction',
              'loss',
              'regularization',
              'subspace',
              'kernel'],
             8: ['flows', 'steady', 'boltzmann', 'law', 'stokes'],
             9: ['numerical',
              'order',
              'element',
              'discretization',
              'differential'],
             10: ['power', 'transmission'

Можем заметить, что модель хорошо справляется с однородностью, согласованностью тем. К примеру ['disease', 'population', 'clinical', 'treatment', 'brain'] можно объединить темой *медицина*, а ['graphs', 'graph', 'tree', 'edges', 'vertex'] - к *работе с графами*. 

Также из этого можно сделать выод, что нам не нужно много слов для описания каждой темы, хватит и нескольких, которые уже будут давать представление о теме в достаточной мере. 

Таким образом мы получили список из 50 основных тем, которые встречаются в нашем датасете. Но пока что от этого мало практической пользы, так как о каждом отдельном документе-статье мы ничего не знаем, а хотели бы понимать к каким темам она относится. 

Поэтому теперь мы соотнесем абстракт каждой статьи с соответствующей для него темой. 

Метод get_thetas возвращает матрицу размера (n_documents, n_topics) с распределением тем для каждого документа. 

In [ ]:
topics_predictions = ctm.get_thetas(training_dataset, n_samples=5) # get all the topic predictions

Sampling: [5/5]: : 5it [02:26, 29.22s/it]


Для начала сделаем это для первой статьи и посмотрим на полученные результаты. 

In [ ]:
topic_number = np.argmax(topics_predictions[0]) # get the topic id of the first document
print('Abstract: ', documents[0])
print('Topic: ', ctm.get_topic_lists(5)[topic_number])

Abstract:    This paper discusses the benefits of describing the world as information,
especially in the study of the evolution of life and cognition. Traditional
studies encounter problems because it is difficult to describe life and
cognition in terms of matter and energy, since their laws are valid only at the
physical scale. However, if matter and energy, as well as life and cognition,
are described in terms of information, evolution can be described consistently
as information becoming more complex.
  The paper presents eight tentative laws of information, valid at multiple
scales, which are generalizations of Darwinian, cybernetic, thermodynamic,
psychological, philosophical, and complexity principles. These are further used
to discuss the notions of life, cognition and their evolution.

Topic:  ['social', 'media', 'community', 'online', 'patterns']


Можем заметить, что хотя тема и не попадает на 100 процентов под описание данной статьи - все равно она примерно описывает корректную область исследования. 

Теперь создадим отдельный столбец в нашем датасете с темами статей. 

In [ ]:
topics_predictions.shape

(43668, 50)

In [ ]:
idx = np.argmax(topics_predictions, axis=1)

topic_ctm = []
for i in range(idx.shape[0]):
  topic_ctm.append(ctm.get_topic_lists(5)[idx[i]])


In [ ]:
papers['topic_ctm'] = topic_ctm
papers

id                                              title  \
0             0704.0304                  The World as Evolving Information   
1             0704.0498  A unified analysis of the reactor neutrino pro...   
2             0704.2768  Heat Equations and the Weighted $\bar\partial$...   
3             0705.0505  Non Supersymmetric Metastable Vacua in N=2 SYM...   
4             0705.0681  Entanglement in a Jaynes-Cummings Model with T...   
...                 ...                                                ...   
43663  quant-ph/0606049  Full security of quantum key distribution from...   
43664  quant-ph/0606131  How many copies are needed for state discrimin...   
43665  quant-ph/9508004  Alternative Derivation of the Hu-Paz-Zhang Mas...   
43666  quant-ph/9809076                  Guiding Neutral Atoms with a Wire   
43667  quant-ph/9908065                   Limits for entanglement measures   

                                                 authors  \
0                                      Carlos Gershenson   
1      Guillaume Mention (DAPNIA), Thierry Lasserre (...   
2                                           Andrew Raich   
3                                       Georgios Pastras   
4                      Samina S. Masood and Allen Miller   
...                                                  ...   
43663  Ll. Masanes, R. Renner, M. Christandl, A. Wint...   
43664                  Aram W. Harrow and Andreas Winter   
43665                             J.J.Halliwell and T.Yu   
43666  Johannes Denschlag, Donatella Cassettari, Joer...   
43667  Michal Horodecki, Pawel Horodecki, and Ryszard...   

                                          authors parsed  \
0                               [[Gershenson, Carlos, ]]   
1      [[Mention, Guillaume, , DAPNIA], [Lasserre, Th...   
2                                    [[Raich, Andrew, ]]   
3                                [[Pastras, Georgios, ]]   
4             [[Masood, Samina S., ], [Miller, Allen, ]]   
...                                                  ...   
43663  [[Masanes, Ll., ], [Renner, R., ], [Christandl...   
43664         [[Harrow, Aram W., ], [Winter, Andreas, ]]   
43665                 [[Halliwell, J. J., ], [Yu, T., ]]   
43666  [[Denschlag, Johannes, ], [Cassettari, Donatel...   
43667  [[Horodecki, Michal, ], [Horodecki, Pawel, ], ...   

                                                abstract  year  \
0        This paper discusses the benefits of describ...  2012   
1        We present in this article a detailed quanti...  2013   
2        The purpose of this article is to establish ...  2012   
3        We find non-supersymmetric metastable vacua ...  2013   
4        We investigate the conditions of entanglemen...  2014   
...                                                  ...   ...   
43663    We analyze a cryptographic protocol for gene...  2014   
43664    Given a collection of states (rho_1, ..., rh...  2012   
43665    Hu, Paz and Zhang [ B.L. Hu, J.P. Paz and Y....  2019   
43666    We demonstrate guiding of cold neutral atoms...  2017   
43667    We show that {\it any} entanglement measure ...  2014   

                                               topic_ctm  
0           [social, media, community, online, patterns]  
1       [nuclear, production, decay, proton, collisions]  
2                     [infty, frac, in, alpha, positive]  
3      [theory, formalism, transformations, theories,...  
4      [quantum, classical, entanglement, codes, chan...  
...                                                  ...  
43663  [quantum, classical, entanglement, codes, chan...  
43664  [probability, random, log, matrices, conditional]  
43665            [flows, steady, boltzmann, law, stokes]  
43666   [785, accumulates, regressive, embryonic, inthe]  
43667  [quantum, classical, entanglement, codes, chan...  

[43668 rows x 7 columns]

Давайте попробуем понять насколько качественно мы кластеризовали наш датасет при помощи модели CombinedTM. Для этого посмотрим на 10 случайных статей и оеним насколько согласованны название и абстракт с полученной темой. 

In [ ]:
papers[['title', 'abstract', 'topic_ctm']].sample(10)

title  \
31559  Entanglement protection in higher-dimensional ...   
27379  Multi-Channel Attention Selection GAN with Cas...   
5079   Random Fluid Limit of an Overloaded Polling Model   
30551  A Full Implementation of Spectro-Perfectionism...   
2161   Hawking radiation as perceived by different ob...   
10242  Proper-Time Hypersurface of Non-Relativistic M...   
6829      Late-replicating CNVs as a source of new genes   
519    On the conjugacy problem for finite-state auto...   
30337  Certified Adversarial Robustness for Deep Rein...   
26047    Differential Privacy for Power Grid Obfuscation   

                                                abstract  \
31559    The inevitable dissipative interaction of an...   
27379    Cross-view image translation is challenging ...   
5079     In the present paper, we study the evolution...   
30551    We present a computationally tractable imple...   
2161     Given a field vacuum state in a black hole s...   
10242    We compute the second-order density fluctuat...   
6829     Asynchronous replication of the genome has b...   
519      We study the conjugacy problem in the automo...   
30337    Deep Neural Network-based systems are now th...   
26047    The availability of high-fidelity energy net...   

                                               topic_ctm  
31559  [quantum, classical, entanglement, codes, chan...  
27379                  [image, object, 3d, images, face]  
5079         [agents, agent, strategies, strategy, game]  
30551       [ray, emission, spectral, sources, detected]  
2161           [scalar, gravity, flat, metric, einstein]  
10242          [scalar, gravity, flat, metric, einstein]  
6829   [disease, population, clinical, treatment, brain]  
519    [category, categorical, categories, modules, lie]  
30337           [ml, machine, real, autonomous, driving]  
26047      [resources, ad, protocol, routing, protocols]

Конечно выборка маленькая и случайная, но даже на ней мы видим, что модель хорошо справилась. 

К примеру статьи про GAN и изображения описываются темой **image, object, 3d, images, face**.  А статья про обучение с подкрепление описывает темой **ml, machine, real, autonomous, driving**. 
 

In [ ]:
topics_ctm = papers[['title', 'abstract', 'topic_ctm']]
topics_ctm.to_csv('topics_ctm.csv', encoding='utf-8')


И напоследок, когда мы уже справились с главной задачей по кластеризации статей, хочется немного вернуться назад и визуализировать полученные темы. Как раз для таких целей существует бибилиотека pyLDAvis - с ее помощью мы сможем интерактивно визуализировать результаты тематического моделирования. 


In [ ]:
 lda_vis_data = ctm.get_ldavis_data_format(qt.vocab, training_dataset, n_samples=10)

Sampling: [10/10]: : 10it [04:40, 28.03s/it]


In [ ]:
!pip install pyLDAvis

In [ ]:
import pyLDAvis as vis
ctm_pd = vis.prepare(**lda_vis_data)
vis.display(ctm_pd)

/usr/local/lib/python3.7/dist-packages/past/types/oldstr.py:5: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import Iterable
/usr/local/lib/python3.7/dist-packages/past/builtins/misc.py:4: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import Mapping
/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


Из чего состоит данная визуализация:
- Каждый пузырь соответствует теме и чем он больше, тем больший процент статей соответствует данной теме
- На голубых строках в графике представлена общая частота каждого слова в корпусе
- На красных строках показано примерное число раз, когда данный термин был создан по заданной теме


Мы можем заметить, что наши темы сгруппировались на две далеких друг от друга части. Но при этом кластеризация получилась довольно равномерной (судя по размерам пузырей) и каждой теме соответствует приблизительно одинаковое количество статетй. 

И на всякий случай сохраним обученную модель. 

In [ ]:
ctm.save(models_dir="./")

/usr/local/lib/python3.7/dist-packages/contextualized_topic_models/models/ctm.py:475: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  Warning)


### Теперь посмотрим на работу модели Zero-Shot Contextualized Topic Model и сравним результаты кластеризации обеих моделей. 

Запускать и обучать модель мы будем аналогично предыдущей. Различия в архитиктере моделей я подробно описывала в теоретической части, поэтому на практике нам важно помнить основные моменты: мы используем "distiluse-base-multilingual-cased" для создания многоязычных контекстуальных эмбеддингов, а сама модель на вход получает только контекстуальные эмбеддинги. 

In [ ]:
tp = TopicModelDataPreparation("distiluse-base-multilingual-cased")
training_dataset2 = tp.fit(text_for_contextual=documents, text_for_bow=preprocessed)

Downloading:   0%|          | 0.00/690 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/114 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.58M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.58M [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/996k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/341 [00:00<?, ?B/s]

/usr/local/lib/python3.7/dist-packages/contextualized_topic_models/utils/data_preparation.py:57: UserWarning: the longest document in your collection has 444 words, the model instead truncates to 128 tokens.
  warnings.warn(f"the longest document in your collection has {max_local_length} words, the model instead "


Batches:   0%|          | 0/219 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


In [ ]:
ctm2 = ZeroShotTM(bow_size=len(tp.vocab), contextual_size=512, n_components=50, num_epochs=15)
ctm2.fit(training_dataset2)

Epoch: [15/15]	 Seen Samples: [655020/655020]	Train Loss: 1029.161393658543	Time: 0:00:30.153204: : 15it [07:45, 31.05s/it]
Sampling: [20/20]: : 20it [09:15, 27.76s/it]


In [ ]:
ctm2.get_topic_lists(5)

[['power', 'multiple', 'channel', 'transmission', 'scheme'],
 ['gauge', 'theories', 'supersymmetric', 'theory', 'symmetries'],
 ['convergence', 'solution', 'differential', 'solving', 'stochastic'],
 ['codes', 'coding', 'rate', 'channels', 'channel'],
 ['consistent', 'star', 'stellar', 'stars', '10'],
 ['disaggregation',
  'unparalleled',
  'assuring',
  'unintentionally',
  'discerning'],
 ['project', 'software', 'business', 'development', 'game'],
 ['stars', 'disk', 'galaxies', 'star', 'galaxy'],
 ['neural', 'training', 'representations', 'deep', 'loss'],
 ['perturbs', 'rejects', 'reprocessed', 'necessitating', 'inaccurately'],
 ['cloud', 'internet', 'security', 'services', 'iot'],
 ['nodes', 'routing', 'node', 'network', 'distributed'],
 ['visual', 'content', 'video', 'retrieval', 'vision'],
 ['graphs', 'vertex', 'vertices', 'every', 'edges'],
 ['temperature', '_2', '_3', 'temperatures', 'diffraction'],
 ['3d', 'reconstruction', 'resolution', 'depth', 'image'],
 ['laser', 'optical', 

In [ ]:
topics_predictions2 = ctm2.get_thetas(training_dataset2, n_samples=5) 
idx2 = np.argmax(topics_predictions2, axis=1)

topic_zero = []
for i in range(idx2.shape[0]):
  topic_zero.append(ctm2.get_topic_lists(5)[idx2[i]])

Sampling: [5/5]: : 5it [02:17, 27.56s/it]


In [ ]:
topics_ctm['topic_zero'] = topic_zero
topics_ctm

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


title  \
0                      The World as Evolving Information   
1      A unified analysis of the reactor neutrino pro...   
2      Heat Equations and the Weighted $\bar\partial$...   
3      Non Supersymmetric Metastable Vacua in N=2 SYM...   
4      Entanglement in a Jaynes-Cummings Model with T...   
...                                                  ...   
43663  Full security of quantum key distribution from...   
43664  How many copies are needed for state discrimin...   
43665  Alternative Derivation of the Hu-Paz-Zhang Mas...   
43666                  Guiding Neutral Atoms with a Wire   
43667                   Limits for entanglement measures   

                                                abstract  \
0        This paper discusses the benefits of describ...   
1        We present in this article a detailed quanti...   
2        The purpose of this article is to establish ...   
3        We find non-supersymmetric metastable vacua ...   
4        We investigate the conditions of entanglemen...   
...                                                  ...   
43663    We analyze a cryptographic protocol for gene...   
43664    Given a collection of states (rho_1, ..., rh...   
43665    Hu, Paz and Zhang [ B.L. Hu, J.P. Paz and Y....   
43666    We demonstrate guiding of cold neutral atoms...   
43667    We show that {\it any} entanglement measure ...   

                                               topic_ctm  \
0           [social, media, community, online, patterns]   
1       [nuclear, production, decay, proton, collisions]   
2                     [infty, frac, in, alpha, positive]   
3      [theory, formalism, transformations, theories,...   
4      [quantum, classical, entanglement, codes, chan...   
...                                                  ...   
43663  [quantum, classical, entanglement, codes, chan...   
43664  [probability, random, log, matrices, conditional]   
43665            [flows, steady, boltzmann, law, stokes]   
43666   [785, accumulates, regressive, embryonic, inthe]   
43667  [quantum, classical, entanglement, codes, chan...   

                                              topic_zero  
0       [project, software, business, development, game]  
1          [rays, shock, radiation, intensity, detector]  
2         [operator, spaces, operators, smooth, sobolev]  
3      [gauge, theories, supersymmetric, theory, symm...  
4      [states, topological, transition, spin, coupling]  
...                                                  ...  
43663           [codes, coding, rate, channels, channel]  
43664                 [in, positive, right, frac, infty]  
43665  [equations, differential, stability, equation,...  
43666  [disaggregation, unparalleled, assuring, unint...  
43667          [vertex, every, vertices, degree, exists]  

[43668 rows x 4 columns]

Снова посмотрим на несколько случайных статей и сравним полученные темы. 

In [63]:
topics_ctm.sample(5)

title  \
20303  Algebraic Description of Shape Invariance Revi...   
39415  Feature Completion for Occluded Person Re-Iden...   
42474             Manipulating Twitter Through Deletions   
5030   Measurement of Permanent Electric Dipole Momen...   
14582  Lens depth function and k-relative neighborhoo...   

                                                abstract  \
20303    We revisit the algebraic description of shap...   
39415    Person re-identification (reID) plays an imp...   
42474    Research into influence campaigns on Twitter...   
5030     Permanent Electric Dipole Moments (EDMs) of ...   
14582    In recent years it has become popular to stu...   

                                               topic_ctm  \
20303  [theory, formalism, transformations, theories,...   
39415                  [image, object, 3d, images, face]   
42474       [social, media, community, online, patterns]   
5030    [nuclear, production, decay, proton, collisions]   
14582  [algorithms, algorithm, search, parallel, clus...   

                                              topic_zero  
20303  [mechanics, quantum, relativity, einstein, the...  
39415     [3d, reconstruction, resolution, depth, image]  
42474   [project, software, business, development, game]  
5030             [qcd, nucleon, quark, chiral, momentum]  
14582  [problems, convergence, function, gaussian, ca...

Постараемся проанализировать полученные результаты. 

Можем заметить, что обе модели хорошо справляются со статьями в области компьютерного зрения, работы с изображениями. Так, к примеру, статью *Feature Completion for Occluded Person Re-Identification* CombinedTM отнесла к теме **image,object,3d,images,face**, а ZeroShotTM к **3d,reconstruction,resolution,depth,image**. 

Логичные темы получились и для статьи *Manipulating Twitter Through Deletions*: **social,media,community,online,patterns** и **project,software,business,development,game**, хотя на мой взгляд первая модель здесь справилась лучше, а у второй получилось лишь приблизительно угадать направление. 

Для статьи *Algebraic Description of Shape Invariance Revisited* модели подобрали темы **theory,formalism,transformations,theories,gauge** и **mechanics,quantum,relativity,einstein,theory**, что соответствует истине, так как статья и правда про теорию и кванотовую механику. 

В целом мы видим, что темы получаются довольно общие и чаще всего 2-3 слова из них и правда описывают соответствующую статью, а некоторые слова уже не очень попадают. 
Также заметим, что темы получаются достаточно однородными и чаще всего слова формируют общее представление о некотором научном исследовательском направлении. 

Сохраним финальный результат. 

In [65]:
topics_ctm.to_csv('topics_res.csv', encoding='utf-8')
# topics_ctm.drop(['abstract'],1).to_csv('topics_res.csv', encoding='utf-8')


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  


In [ ]:
lda_vis_data = ctm2.get_ldavis_data_format(tp.vocab, training_dataset2, n_samples=10)
ctm_pd = vis.prepare(**lda_vis_data)
vis.display(ctm_pd)

0it [01:44, ?it/s]
Sampling: [10/10]: : 10it [04:44, 28.50s/it]
/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


Заметим, что в работе мы не пользовались главным свойством данной модели - многоязычностью, так как весь датасет представлен на одном английском языке. 

Из визуализации мы видим, что результаты работы обеих моделей довольно похожи. 